In [1]:

import os  # #
#from data_processing.Extract_Interface import Extract_Interface
import numpy as np
np.set_printoptions(suppress=True)  # 取消科学计数法输出
np.set_printoptions(threshold = np.inf)
import math
import operator
from functools import reduce
from scipy.spatial import distance_matrix
ee=math.e
import torch

/home/yanzh/anaconda3/envs/glydeep/lib/python3.8/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
#先处理A链
all_path_A='/data5_large/home/yanzh/deeplearn/graph_residue/my_data/protein_new_3222/dataset_shuanglian_buchong/a_picture/train/A/all'
pos_path_A='/data5_large/home/yanzh/deeplearn/graph_residue/my_data/protein_new_3222/dataset_shuanglian_buchong/a_picture/train/A/pos'
neg_path_A='/data5_large/home/yanzh/deeplearn/graph_residue/my_data/protein_new_3222/dataset_shuanglian_buchong/a_picture/train/A/neg'
all_new_path_A='/data5_large/home/yanzh/deeplearn/graph_residue/my_data/protein_new_3222/dataset_shuanglian_buchong/a_picture/train/A/renew/all'
neg_new_path_A='/data5_large/home/yanzh/deeplearn/graph_residue/my_data/protein_new_3222/dataset_shuanglian_buchong/a_picture/train/A/renew/neg'
all_path_A_sasa='/data5_large/home/yanzh/deeplearn/graph_residue/my_data/protein_new_3222/dataset_shuanglian_buchong/a_picture/train/A/all/sasa'
pos_path_A_sasa='/data5_large/home/yanzh/deeplearn/graph_residue/my_data/protein_new_3222/dataset_shuanglian_buchong/a_picture/train/A/pos/sasa'
neg_path_A_sasa='/data5_large/home/yanzh/deeplearn/graph_residue/my_data/protein_new_3222/dataset_shuanglian_buchong/a_picture/train/A/neg/sasa'
all_new_path_A_sasa='/data5_large/home/yanzh/deeplearn/graph_residue/my_data/protein_new_3222/dataset_shuanglian_buchong/a_picture/train/A/renew/all/sasa'
neg_new_path_A_sasa='/data5_large/home/yanzh/deeplearn/graph_residue/my_data/protein_new_3222/dataset_shuanglian_buchong/a_picture/train/A/renew/neg/sasa'
save_npz_path='/data5_large/home/yanzh/deeplearn/graph_residue/my_data/protein_new_3222/dataset_shuanglian_buchong/a_picture5/train/npz'

In [3]:
#再处理B链
all_path_B='/data5_large/home/yanzh/deeplearn/graph_residue/my_data/protein_new_3222/dataset_shuanglian_buchong/a_picture/train/B/all'
pos_path_B='/data5_large/home/yanzh/deeplearn/graph_residue/my_data/protein_new_3222/dataset_shuanglian_buchong/a_picture/train/B/pos'
neg_path_B='/data5_large/home/yanzh/deeplearn/graph_residue/my_data/protein_new_3222/dataset_shuanglian_buchong/a_picture/train/B/neg'
all_new_path_B='/data5_large/home/yanzh/deeplearn/graph_residue/my_data/protein_new_3222/dataset_shuanglian_buchong/a_picture/train/B/renew/all'
neg_new_path_B='/data5_large/home/yanzh/deeplearn/graph_residue/my_data/protein_new_3222/dataset_shuanglian_buchong/a_picture/train/B/renew/neg'
all_path_B_sasa='/data5_large/home/yanzh/deeplearn/graph_residue/my_data/protein_new_3222/dataset_shuanglian_buchong/a_picture/train/B/all/sasa'
pos_path_B_sasa='/data5_large/home/yanzh/deeplearn/graph_residue/my_data/protein_new_3222/dataset_shuanglian_buchong/a_picture/train/B/pos/sasa'
neg_path_B_sasa='/data5_large/home/yanzh/deeplearn/graph_residue/my_data/protein_new_3222/dataset_shuanglian_buchong/a_picture/train/B/neg/sasa'
all_new_path_B_sasa='/data5_large/home/yanzh/deeplearn/graph_residue/my_data/protein_new_3222/dataset_shuanglian_buchong/a_picture/train/B/renew/all/sasa'
neg_new_path_B_sasa='/data5_large/home/yanzh/deeplearn/graph_residue/my_data/protein_new_3222/dataset_shuanglian_buchong/a_picture/train/B/renew/neg/sasa'

In [4]:
interface_rec_list = [f for f in os.listdir(pos_path_A) if f.endswith('.pdb')]
interface_rec_list.sort()

In [5]:
MaxASA = {  
        "ALA": 129.0,  # Alanine  
        "ARG": 274.0,  # Arginine  
        "ASN": 195.0,  # Asparagine  
        "ASP": 193.0,  # Aspartate (Aspartic acid)  
        "CYS": 167.0,  # Cysteine  
        "GLU": 223.0,  # Glutamate (Glutamic acid)  
        "GLN": 225.0,  # Glutamine  
        "GLY": 104.0,  # Glycine  
        "HIS": 224.0,  # Histidine  
        "ILE": 197.0,  # Isoleucine  
        "LEU": 201.0,  # Leucine  
        "LYS": 236.0,  # Lysine  
        "MET": 224.0,  # Methionine  
        "PHE": 240.0,  # Phenylalanine  
        "PRO": 159.0,  # Proline  
        "SER": 155.0,  # Serine  
        "THR": 172.0,  # Threonine  
        "TRP": 285.0,  # Tryptophan  
        "TYR": 263.0,  # Tyrosine  
        "VAL": 174.0   # Valine  
        }  

amino_acid_order = [
    'CYS', 'SER', 'THR', 'PRO', 'ALA', 'GLY', 'ASN', 'ASP', 'GLU', 'GLN',
    'HIS', 'ARG', 'LYS', 'MET', 'ILE', 'LEU', 'VAL', 'PHE', 'TYR', 'TRP']

In [6]:
def read_frequency_table(file_path):
    """
    读取频率分布表
    :param file_path: 频率分布表文件路径
    :return: 频率矩阵
    """
    frequency_matrix = []
    try:
        with open(file_path, 'r') as file:
            lines = file.readlines()
            # 跳过表头
            for line in lines[1:]:
                # 跳过第一列的氨基酸名称
                row = [int(val) for val in line.strip().split('\t')[1:]]
                frequency_matrix.append(row)
    except FileNotFoundError:
        print(f"未找到频率分布表文件: {file_path}")
    return np.array(frequency_matrix)

def calculate_exposed_residues(sasa_file_path, pdb_file_path, threshold=0.5):
    """
    计算给定 SASA 文件中暴露的 CA 原子的索引
    :param sasa_file_path: SASA 文件路径
    :param pdb_file_path: PDB 文件路径
    :param threshold: RSA 阈值，默认为 0.1
    :return: 暴露 CA 原子的索引列表
    """
    sasa_data = []
    try:
        with open(sasa_file_path, 'r') as rec_file:
            for line in rec_file:
                if line.startswith('SEQ'):
                    try:
                        residue_name = line[12:15].strip()
                        sasa_value = float(line[19:26].strip())
                        sasa_data.append((residue_name, sasa_value))
                    except (ValueError, IndexError):
                        print(f"解析行 '{line.strip()}' 时出错，跳过该行。")
    except FileNotFoundError:
        print(f"未找到文件: {sasa_file_path}")

    exposed_indices = []
    ca_index = 0
    with open(pdb_file_path, 'r') as pdb_file:
        for line in pdb_file:
            if line[:4] == 'ATOM' and line[12:16].strip() == 'C':
                if ca_index < len(sasa_data):
                    exposed_indices.append(ca_index)
                ca_index += 1
    print(exposed_indices)
    return exposed_indices, sasa_data


def get_c_coordinates(pdb_file):
    """
    从 PDB 文件中获取所有 CA 原子的坐标
    :param pdb_file: PDB 文件路径
    :return: CA 原子坐标的 numpy 数组
    """
    ca_accord = []
    with open(pdb_file, 'r') as file:
        lines = file.readlines()
        for line in lines:
            if line[:4] == 'ATOM' and line[12:16].strip() == 'C':
                x = float(line[31:38])
                y = float(line[39:46])
                z = float(line[47:54])
                ca_accord.append([x, y, z])
    return np.array(ca_accord)

In [7]:

for num2,numm in enumerate(interface_rec_list):
    if numm[5] != '1':
        continue
    #if numm !='1ibr_A.pdb':
    #    continue
    pdb_name=numm[0:10]
    
    A_chain=pdb_name[-1]
    B_chain=pdb_name[-3]
    
    numm2 = f'{pdb_name}_{B_chain}.pdb'
    interface_pdb_A=numm     # xxxx.pdb
    pdbid_A=interface_pdb_A.replace('.pdb','')
    interface_pdb_B=numm2
    pdbid_B=interface_pdb_B.replace('.pdb','')
    
    
    all_pdb=os.path.join(all_path_A,interface_pdb_A)
    pos_pdb=os.path.join(pos_path_A,interface_pdb_A)
    neg_pdb=os.path.join(neg_path_A,interface_pdb_A)
    all_new_pdb=os.path.join(all_new_path_A,interface_pdb_A)
    neg_new_pdb=os.path.join(neg_new_path_A,interface_pdb_A)
    print('目前正在处理的是：%s'%interface_pdb_A)
    all_sasa=os.path.join(all_path_A_sasa,interface_pdb_A)
    all_new_sasa=os.path.join(all_new_path_A_sasa,interface_pdb_A)
    pos_sasa=os.path.join(pos_path_A_sasa,interface_pdb_A)
    neg_sasa=os.path.join(neg_path_A_sasa,interface_pdb_A)
    neg_new_sasa=os.path.join(neg_new_path_A_sasa,interface_pdb_A)
    
    all_pdb_B=os.path.join(all_path_B,interface_pdb_B)
    pos_pdb_B=os.path.join(pos_path_B,interface_pdb_B)
    neg_pdb_B=os.path.join(neg_path_B,interface_pdb_B)
    all_new_pdb_B=os.path.join(all_new_path_B,interface_pdb_B)
    neg_new_pdb_B=os.path.join(neg_new_path_B,interface_pdb_B)
    print('目前正在处理的是：%s'%interface_pdb_B)
    all_sasa_B=os.path.join(all_path_B_sasa,interface_pdb_B)
    all_new_sasa_B=os.path.join(all_new_path_B_sasa,interface_pdb_B)
    pos_sasa_B=os.path.join(pos_path_B_sasa,interface_pdb_B)
    neg_sasa_B=os.path.join(neg_path_B_sasa,interface_pdb_B)
    neg_new_sasa_B=os.path.join(neg_new_path_B_sasa,interface_pdb_B)
    frequency_file_path='/data5_large/home/yanzh/deeplearn/graph_residue/my_data/protein_new_3222/dataset_shuanglian_buchong/a_picture2/氨基酸理化性质分布.py'
    esm_feature=torch.load(f'/data5_large/home/yanzh/deeplearn/graph_residue/my_data/protein_new_3222/dataset_shuanglian_buchong/a_picture/train/hebin_esm/{pdb_name}_{A_chain}.pt')
    ems_33 = esm_feature['representations'][33] 
    print(np.shape(ems_33))
    
    frequency_matrix = read_frequency_table(frequency_file_path)
    
    ####################################################节点特征计算######################################################################################
        ################negative_residues_Shanchu——A获取#####################################3
    negative_residues_Shanchu=[]
    all_residues_tuples=[]
    neg_resid=[]
    with open(neg_sasa,'r') as rec_file:
        line = rec_file.readlines() 
        for i in line:
            if i[0:3] =='SEQ':
                i=i.strip()
                bb=i[12:15]         #残基名称
                dd=i[6:11].strip()   #残基编号
                cc=float(i[19:26])   #sasa
            #print(bb,cc)            # 将文件中的SASA值存储到字典中  
                #negative_residues_tuples.append((dd,bb,cc))
                neg_resid.append(dd)
    
    with open(all_sasa,'r') as rec_file2:
        line = rec_file2.readlines() 
        for i in line:
            if i[0:3] =='SEQ':
                i=i.strip()
                bb=i[12:15]         #残基名称
                dd=i[6:11].strip()   #残基编号
                cc=float(i[19:26])   #sasa
            #print(bb,cc)            # 将文件中的SASA值存储到字典中  
                all_residues_tuples.append((dd,bb,cc))
    for residue_id,residue_name,residue_value in all_residues_tuples:
        if residue_id in neg_resid:
            if residue_name in MaxASA:
                result= residue_value/MaxASA[residue_name]
                if result < 0.2:
                    negative_residues_Shanchu.append(residue_id)
                    
                    
                    
        ################negative_residues_Shanchu——B获取#####################################3
    negative_residues_Shanchu_B=[]
    all_residues_tuples_B=[]
    neg_resid_B=[]
    with open(neg_sasa_B,'r') as rec_file:
        line = rec_file.readlines() 
        for i in line:
            if i[0:3] =='SEQ':
                i=i.strip()
                bb=i[12:15]         #残基名称
                dd=i[6:11].strip()   #残基编号
                cc=float(i[19:26])   #sasa
            #print(bb,cc)            # 将文件中的SASA值存储到字典中  
                #negative_residues_tuples.append((dd,bb,cc))
                neg_resid_B.append(dd)
    
    with open(all_sasa_B,'r') as rec_file2:
        line = rec_file2.readlines() 
        for i in line:
            if i[0:3] =='SEQ':
                i=i.strip()
                bb=i[12:15]         #残基名称
                dd=i[6:11].strip()   #残基编号
                cc=float(i[19:26])   #sasa
            #print(bb,cc)            # 将文件中的SASA值存储到字典中  
                all_residues_tuples_B.append((dd,bb,cc))
    for residue_id,residue_name,residue_value in all_residues_tuples_B:
        if residue_id in neg_resid_B:
            if residue_name in MaxASA:
                result= residue_value/MaxASA[residue_name]
                if result < 0.2:
                    negative_residues_Shanchu_B.append(residue_id)
        #############esm特征重新获取-A########################
    all_resid=[]
    postive_resid=[]
    with open(all_sasa,'r') as rec_file:
        line1 = rec_file.readlines() 
    for i in line1:
            if i[0:3] =='SEQ':
                i=i.strip()
                bb=i[12:15]
                dd=i[6:11].strip()
                cc=float(i[19:26])
                all_resid.append(dd)  
        
    with open(all_new_sasa,'r') as rec_file:
        line2 = rec_file.readlines() 
    for i in line2:
            if i[0:3] =='SEQ':
                i=i.strip()
                bb=i[12:15]
                dd=i[6:11].strip()
                cc=float(i[19:26])
                postive_resid.append(dd)  
    yy=[]
    for i,value in enumerate(all_resid):
        if value in postive_resid:
            yy.append(i)
            
            
        #############esm特征重新获取-B########################    
    all_resid_B=[]
    postive_resid_B=[]
    with open(all_sasa_B,'r') as rec_file:
        line1 = rec_file.readlines() 
    for i in line1:
            if i[0:3] =='SEQ':
                i=i.strip()
                bb=i[12:15]
                dd=i[6:11].strip()
                cc=float(i[19:26])
                all_resid_B.append(dd)  
        
    with open(all_new_sasa_B,'r') as rec_file:
        line2 = rec_file.readlines() 
    for i in line2:
            if i[0:3] =='SEQ':
                i=i.strip()
                bb=i[12:15]
                dd=i[6:11].strip()
                cc=float(i[19:26])
                postive_resid_B.append(dd)  
    #print('postive_resid_B',postive_resid_B)
    
    yy_A=[]
    for i,value in enumerate(all_resid):
        if value in postive_resid:
            yy_A.append(i)  
   
    yy_B=[]
    for i,value in enumerate(all_resid_B):
        if value in postive_resid_B:
            yy_B.append(i)  
    #print(yy_B,len(yy_B))
    #print('postive_resid_B',len(postive_resid_B))
            
    A_len=len(all_resid)
    A_ems=ems_33[0:A_len]
    #print('A_ems...',np.shape(A_ems))
    B_ems=ems_33[A_len:]
    #print('B_ems...',np.shape(B_ems))

    
    A_ems_new=A_ems[yy_A]
    #print('A_ems_new',np.shape(A_ems_new))
    B_ems_new=B_ems[yy_B]
    #print('B_ems_new',np.shape(B_ems_new))
    esm_all=torch.cat((A_ems_new,B_ems_new),dim=0)
    
    ####################################归一化#############################################
    def dic_normalize(dic): #计算方法为：该值-最小值/最大值-最小值  归一化 
            #print(dic)
            max_value = dic[max(dic, key=dic.get)]
            min_value = dic[min(dic, key=dic.get)]
            #print(max_value)
            #print(min_value)
            interval = float(max_value) - float(min_value)
            #print('interval',interval)
            for key in dic.keys():
                dic[key] = round((dic[key] - min_value) / interval,4)
            dic['X'] = (max_value + min_value) / 2.0  #在字典中添加X 记录为最大值和最小值的平均值
            return dic
    # 归一化
    def normalize_pssm(value):        #position specific scoring matrix 位置特异性评分矩阵
            pssm=1/(1+ee**-value)
            pssm=round(pssm,4)
            return pssm
        
    pro_res_table = ['ALA ', 'CYS ', 'ASP ', 'GLU ', 'PHE ', 'GLY ', 'HIS ', 'ILE ', 'LYS ', 'LEU ', 'MET ', 'ASN ', 'PRO ', 'GLN ', 
                         'ARG ', 'SER ', 
                         'THR ', 'VAL ', 'TRP ', 'TYR ']
        #Whether the residue is aliphatic(脂肪族氨基酸)
    pro_res_aliphatic_table = ['ALA ', 'ILE ', 'LEU ', 'MET ', 'VAL ']
        #Whether the residue is aromatic（芳香性氨基酸）
    pro_res_aromatic_table = ['PHE ', 'TRP ', 'TYR ']
        #Whether the residue is polar neutral（中性氨基酸）
    pro_res_polar_neutral_table = ['CYS ', 'ASN ', 'GLN ', 'SER ', 'THR ']
        #Whether the residue is acidic charged（酸性氨基酸）
    pro_res_acidic_charged_table = ['ASP ', 'GLU ']
        #Whether the residue is basic charged（碱性氨基酸）
    pro_res_basic_charged_table = ['HIS ', 'LYS ', 'ARG ']
        #Residue weight（分子量）
    res_weight_table = {'ALA ': 71.08, 'CYS ': 103.15, 'ASP ': 115.09, 'GLU ': 129.12, 'PHE ': 147.18, 'GLY ': 57.05, 'HIS ': 137.14,
                                        'ILE ': 113.16, 'LYS ': 128.18, 'LEU ': 113.16, 'MET ': 131.20, 'ASN ': 114.11, 'PRO ': 97.12, 'GLN ': 128.13,
                                        'ARG ': 156.19, 'SER ': 87.08, 'THR ': 101.11, 'VAL ': 99.13, 'TRP ': 186.22, 'TYR ': 163.18}
        #The negative of the logarithm of the dissociation constant for the –COOH group（羧基的解离常数的负对数pK1）
    res_pka_table = {'ALA ': 2.34, 'CYS ': 1.96, 'ASP ': 1.88, 'GLU ': 2.19, 'PHE ': 1.83, 'GLY ': 2.34, 'HIS ': 1.82, 'ILE ': 2.36,
                                     'LYS ': 2.18, 'LEU ': 2.36, 'MET ': 2.28, 'ASN ': 2.02, 'PRO ': 1.99, 'GLN ': 2.17, 'ARG ': 2.17, 'SER ': 2.21,
                                     'THR ': 2.09, 'VAL ': 2.32, 'TRP ': 2.83, 'TYR ': 2.32}
        #The negative of the logarithm of the dissociation constant for the –NH3 group（氨基的解离常数的负对数pK2）
    res_pkb_table = {'ALA ': 9.69, 'CYS ': 10.28, 'ASP ': 9.60, 'GLU ': 9.67, 'PHE ': 9.13, 'GLY ': 9.60, 'HIS ': 9.17,
                 'ILE ': 9.60, 'LYS ': 8.95, 'LEU ': 9.60, 'MET ': 9.21, 'ASN ': 8.80, 'PRO ': 10.60, 'GLN ': 9.13,
                 'ARG ': 9.04, 'SER ': 9.15, 'THR ': 9.10, 'VAL ': 9.62, 'TRP ': 9.39, 'TYR ': 9.62}
        #The pH at the isoelectric point（等电点）
    res_pl_table = {'ALA ': 6.00, 'CYS ': 5.07, 'ASP ': 2.77, 'GLU ': 3.22, 'PHE ': 5.48, 'GLY ': 5.97, 'HIS ': 7.59,
                        'ILE ': 6.02, 'LYS ': 9.74, 'LEU ': 5.98, 'MET ': 5.74, 'ASN ': 5.41, 'PRO ': 6.30, 'GLN ': 5.65,
                        'ARG ': 10.76, 'SER ': 5.68, 'THR ': 5.60, 'VAL ': 5.96, 'TRP ': 5.89, 'TYR ': 5.96}
        #Hydrophobicity of residue (pH=2)
    res_hydrophobic_ph2_table = {'ALA ': 47, 'CYS ': 52, 'ASP ': -18, 'GLU ': 8, 'PHE ': 92, 'GLY ': 0, 'HIS ': -42, 'ILE ': 100,
                                     'LYS ': -37, 'LEU ': 100, 'MET ': 74, 'ASN ': -41, 'PRO ': -46, 'GLN ': -18, 'ARG ': -26, 'SER ': -7,
                                     'THR ': 13, 'VAL ': 79, 'TRP ': 84, 'TYR ': 49}
        #Hydrophobicity of residue (pH=7)
    res_hydrophobic_ph7_table = {'ALA ': 41, 'CYS ': 49, 'ASP ': -55, 'GLU ': -31, 'PHE ': 100, 'GLY ': 0, 'HIS ': 8, 'ILE ': 99,
                                 'LYS ': -23, 'LEU ': 97, 'MET ': 74, 'ASN ': -28, 'PRO ': -46, 'GLN ': -10, 'ARG ': -14, 'SER ': -5,
                                 'THR ': 13, 'VAL ': 76, 'TRP ': 97, 'TYR ': 63}
    res_weight_table = dic_normalize(res_weight_table)
    res_pka_table = dic_normalize(res_pka_table)
    res_pkb_table =dic_normalize(res_pkb_table)
    res_pl_table =dic_normalize(res_pl_table)
    res_hydrophobic_ph2_table =dic_normalize(res_hydrophobic_ph2_table)
    res_hydrophobic_ph7_table = dic_normalize(res_hydrophobic_ph7_table)
    def one_of_k_encoding(x, allowable_set):
            if x not in allowable_set:
                # print(x)
                raise Exception('input {0} not in allowable set{1}:'.format(x, allowable_set))
            return list(map(lambda s: x == s, allowable_set))
    
    def residue_features(residue):
            res_property1 = [1 if residue in pro_res_aliphatic_table else 0, 
                                1 if residue in pro_res_aromatic_table else 0,
                                1 if residue in pro_res_polar_neutral_table else 0,
                                1 if residue in pro_res_acidic_charged_table else 0,
                                1 if residue in pro_res_basic_charged_table else 0]
            res_property2 = [res_weight_table[residue], res_pka_table[residue], res_pkb_table[residue], res_pl_table[residue]]
            #print(np.array(res_property1 + res_property2+res_property3).shape)
            #return np.array(res_property1 + res_property2+res_property3)
            features=(res_property1 + res_property2)
            return features
        
    ######################节点特征计算-A######################
    
    value1=[]
    res_list=[]
    value3=[]
    res_list2=[]
    with open(all_sasa,'r') as rec_file:
            line = rec_file.readlines()
            for x in line[1:-1]:
                x=x.strip()
                resid=x[12:16]   #氨基酸的名称
                sasa_value=x[19:26]  #溶剂可及表面积
                dd=x[6:11].strip()   #氨基酸号
                value1.append(sasa_value)
                res_list.append(resid)  #氨基酸名称
                if dd  in postive_resid:
                    value3.append(sasa_value)
                    res_list2.append(resid)
    maxnum=float(max(value1))
    minnum=float(min(value1))
    internal_value=maxnum-minnum
    value2=[]
    for x1 in value3:
            x1=float(x1)
            final_value=round((x1-minnum)/internal_value,4)  #归一化，将数值归一到0-1之间，保留四位小数
                    #print(final_value)
            value2.append(final_value)   #final_value为sasa归一化后的值
            
            
    rec_fea=[]
    if len(value2)==len(res_list2):
            for m in range(len(value2)):
                sasa=[value2[m]]   #sasa为归一化后的值
                pro_seq=[res_list2[m]]  #氨基酸名称
                resid=res_list2[m]
                pro_hot=np.zeros((1,len(pro_res_table)))   #1行20列的全零矩阵
                for i in range(len(pro_seq)):  #i=1
                    pro_hot[i,] = one_of_k_encoding(pro_seq[i], pro_res_table)
                pro_hot1=reduce(operator.add, pro_hot)  #将二维将至一维
                pro_hot1=pro_hot1.tolist()  #将矩阵转化为列表，以便下面的特征合并
                rec_feature=residue_features(resid)
                rec_fea.append(pro_hot1+rec_feature+sasa)  #每一个氨基酸的特征
            rec_fea=np.array(rec_fea)    
    rec_fea_tensor = torch.from_numpy(rec_fea) 
    
    
    ######################节点特征计算-B######################
    #print('negative_residues_Shanchu_B',negative_residues_Shanchu_B)
    value1_B=[]
    res_list_B=[]
    value3_B=[]
    res_list2_B=[]
    with open(all_sasa_B,'r') as rec_file:
            line = rec_file.readlines()
            for x in line[1:-1]:
                x=x.strip()
                resid=x[12:16]   #氨基酸的名称
                sasa_value=x[19:26]  #溶剂可及表面积
                dd=x[6:11].strip()   #氨基酸号
                value1_B.append(sasa_value)
                res_list_B.append(resid)  #氨基酸名称
                if dd  in postive_resid_B:
                    value3_B.append(sasa_value)
                    res_list2_B.append(resid)
    maxnum=float(max(value1_B))
    minnum=float(min(value1_B))
    internal_value=maxnum-minnum
    value2_B=[]
    for x1 in value3_B:
            x1=float(x1)
            final_value=round((x1-minnum)/internal_value,4)  #归一化，将数值归一到0-1之间，保留四位小数
                    #print(final_value)
            value2_B.append(final_value)   #final_value为sasa归一化后的值
            
            
    rec_fea=[]
    if len(value2_B)==len(res_list2_B):
            for m in range(len(value2_B)):
                sasa=[value2_B[m]]   #sasa为归一化后的值
                pro_seq=[res_list2_B[m]]  #氨基酸名称
                resid=res_list2_B[m]
                pro_hot=np.zeros((1,len(pro_res_table)))   #1行20列的全零矩阵
                for i in range(len(pro_seq)):  #i=1
                    pro_hot[i,] = one_of_k_encoding(pro_seq[i], pro_res_table)
                pro_hot1=reduce(operator.add, pro_hot)  #将二维将至一维
                pro_hot1=pro_hot1.tolist()  #将矩阵转化为列表，以便下面的特征合并
                rec_feature=residue_features(resid)
                rec_fea.append(pro_hot1+rec_feature+sasa)  #每一个氨基酸的特征
            rec_fea=np.array(rec_fea)    
    rec_fea_tensor_B = torch.from_numpy(rec_fea)
    
    #print('rec_fea_tensor',np.shape(rec_fea_tensor))
    #print('rec_fea_tensor_B',np.shape(rec_fea_tensor_B))
    
    
    rec_lig_feature = torch.cat((rec_fea_tensor, rec_fea_tensor_B), dim=0)
    #print('初步合并后的特征矩阵大小为：',np.shape(rec_lig_feature))
    
    #print(np.shape(esm_all))
    final_feature = torch.cat((rec_lig_feature, esm_all), dim=1)
    #print('最后合并后的特征矩阵的大小为：',np.shape(final_feature))
    
    
    
    #################################################3333距离特征计算##############################################
    
    ###############距离特征的计算-A######################33
    ca_accord_rec=[]
    residues = {} 
    a=0
    with open(all_new_pdb, 'r') as file:  
                    for line in file:  
                        if line.startswith('ATOM'):  
                            # 解析PDB行的关键信息  
                            atom_name = line[12:16].strip()  
                            residue_name = line[17:20].strip()  
                            chain_id = line[21].strip()  
                            residue_number = (line[22:27].strip())  
                            x = float(line[30:38].strip())  
                            y = float(line[38:46].strip())  
                            z = float(line[46:54].strip())  
                
                            # 检查是否是CA原子  
                            if atom_name == 'CA': ##太离谱了，有的没有CA有的多个CA,....................................... 
                                # 如果这是当前氨基酸的第一个CA，则存储它  
                                a+=1
                                if (chain_id, residue_number) not in residues:  
                                    residues[(chain_id, residue_number)] = (x, y, z)  
    for (chain_id, residue_number), (x, y, z) in residues.items():  
            ca_accord_rec.append([x]+[y]+[z])
            #print(residues)            
            #print(ca_accord_rec)
            a+=1
    ca_accord_rec=np.array(ca_accord_rec)

    dis_rec_rec_A = distance_matrix(ca_accord_rec, ca_accord_rec)
        #算出来的距离进行处理，受体-受体和配体-配体之间的距离小于4.5为1，受体-配体之间的距离小于10为1
    for ii in np.nditer(dis_rec_rec_A,op_flags=['readwrite']):
            if ii >8.0:
                ii[...]=0
            else:
                ii[...]=1
                
    a1=rec_fea_tensor.shape
    a2=dis_rec_rec_A.shape
    a11=a1[0]
    a22=a2[0]
    print(f'A链的特征矩阵的大小为:{a1},A链的邻接矩阵的小为{a2}')
    if a11!=a22:
            print(interface_pdb_A,'A链有问题###################################################################')
            print(a1)
            print(a2)
    sA=np.shape(dis_rec_rec_A)
    lenth1=sA[0]
    width1=sA[1]
    
    
    
    ###############距离特征的计算-B######################33
    
    ca_accord_rec_B=[]
    residues_B = {} 
    a=0
    with open(all_new_pdb_B, 'r') as file:  
                    for line in file:  
                        if line.startswith('ATOM'):  
                            # 解析PDB行的关键信息  
                            atom_name = line[12:16].strip()  
                            residue_name = line[17:20].strip()  
                            chain_id = line[21].strip()  
                            residue_number = (line[22:27].strip())  
                            x = float(line[30:38].strip())  
                            y = float(line[38:46].strip())  
                            z = float(line[46:54].strip())  
                
                            # 检查是否是CA原子  
                            if atom_name == 'CA': ##太离谱了，有的没有CA有的多个CA,....................................... 
                                # 如果这是当前氨基酸的第一个CA，则存储它  
                                a+=1
                                if (chain_id, residue_number) not in residues_B:  
                                    residues_B[(chain_id, residue_number)] = (x, y, z)  
    for (chain_id, residue_number), (x, y, z) in residues_B.items():  
            ca_accord_rec_B.append([x]+[y]+[z])
            #print(residues)            
            #print(ca_accord_rec)
            a+=1
    ca_accord_rec_B=np.array(ca_accord_rec_B)
    dis_rec_rec_B = distance_matrix(ca_accord_rec_B, ca_accord_rec_B)
        #算出来的距离进行处理，受体-受体和配体-配体之间的距离小于4.5为1，受体-配体之间的距离小于10为1
    for ii in np.nditer(dis_rec_rec_B,op_flags=['readwrite']):
            if ii >8.0:
                ii[...]=0
            else:
                ii[...]=1
                
    a1=rec_fea_tensor_B.shape
    a2=dis_rec_rec_B.shape
    a11=a1[0]
    a22=a2[0]
    print(f'B链的特征矩阵的大小为:{a1},B链的邻接矩阵的小为{a2}')
    if a11!=a22:
            print(interface_pdb_B,'有问题###################################################################')
            print(a1)
            print(a2)
    sB=np.shape(dis_rec_rec_B)
    lenth2=sB[0]
    width2=sB[1]
    print(f'lenth2的长度为：',lenth2,'lenth1的长度为：',lenth1)
    combined_matrix = np.zeros((lenth1+lenth2, lenth1+lenth2))
    combined_matrix[:lenth1, :lenth1] = dis_rec_rec_A
    combined_matrix[lenth1:, lenth1:] = dis_rec_rec_B
    print('合并后的邻接矩阵大小combined_matrix为：',np.shape(combined_matrix))
    
    
    #recA_c_count = len(get_c_coordinates(all_new_pdb))
    #recB_c_count = len(get_c_coordinates(all_new_pdb_B))
    
    #print(recA_c_count,recB_c_count)
    #print(f'recA_c_count的长度为{recA_c_count}，recB_c_count的长度为{recB_c_count}')
    
    exposed_rec1, sasa_data_rec1 = calculate_exposed_residues(all_new_sasa, all_new_pdb)
    exposed_rec2, sasa_data_rec2 = calculate_exposed_residues(all_new_sasa_B, all_new_pdb_B)
    #print(sasa_data_rec1)
    #print(sasa_data_rec2)
    #print(exposed_rec1)
    frequency_matrix = read_frequency_table(frequency_file_path)
    
    adj_matrix = np.zeros((len(exposed_rec1),len(exposed_rec2)))
    for i,idx1 in enumerate(exposed_rec1):
        residue_name1 = sasa_data_rec1[idx1][0]
        for j,idx2 in enumerate(exposed_rec2):
            residue_name2 = sasa_data_rec2[idx2][0]
            try:
                amino_acid_index1 = amino_acid_order.index(residue_name1)
                amino_acid_index2 = amino_acid_order.index(residue_name2)
            
                if frequency_matrix[amino_acid_index1,amino_acid_index2] > 0:
                    adj_matrix[i,j] = 1
            except ValueError:
                continue
            
    for i ,idx1 in enumerate(exposed_rec1): 
        for j ,idx2 in enumerate(exposed_rec2):
            combined_matrix[idx1,lenth1+idx2] =adj_matrix[i,j]   
            combined_matrix[lenth1 + idx2, idx1] = adj_matrix[i, j]   
    #print('合并后的邻接矩阵大小为：', combined_matrix.shape)
    #print(combined_matrix)
    
    
        
    ################################标签计算-A ####################################################
    all_target=[]
    with open(all_new_sasa,'r') as tar_file:
            line=tar_file.readlines()
            for i in line[1:-1]:
                i=i.strip() 
                all_id=i[6:11]  #str
                all_target.append(all_id)
    #print(all_target)
    pos_target=[]
    with open(pos_sasa,'r') as tar_file1:
            line1=tar_file1.readlines()
            for i1 in line1[1:-1]:
                i1=i1.strip() 
                pos_id=i1[6:11]
                pos_target.append(pos_id)
    #print(pos_target)
    neg_target=[]
    with open(neg_new_sasa,'r') as tar_file2:
            line2=tar_file2.readlines()
            for i2 in line2[1:-1]:
                i2=i2.strip() 
                neg_id=i2[6:11]
                neg_target.append(neg_id)
    #print(neg_target)
    tt=all_target
    new_target=all_target
        
                #print(new_target)
    for numm,i55 in enumerate(tt):
                    for i66 in neg_target:
                        if i66==i55:
                            new_target[numm]=0
    for num,i5 in enumerate(tt):
                    for i6 in pos_target:
                        if i6==i5:
                            new_target[num]=1 
    
    
    ################################标签计算-B ####################################################
    all_target_B=[]
    with open(all_new_sasa_B,'r') as tar_file:
            line=tar_file.readlines()
            for i in line[1:-1]:
                i=i.strip() 
                all_id=i[6:11]  #str
                all_target_B.append(all_id)
    #print(all_target)
    pos_target_B=[]
    with open(pos_sasa_B,'r') as tar_file1:
            line1=tar_file1.readlines()
            for i1 in line1[1:-1]:
                i1=i1.strip() 
                pos_id=i1[6:11]
                pos_target_B.append(pos_id)
    #print(pos_target)
    neg_target_B=[]
    with open(neg_new_sasa_B,'r') as tar_file2:
            line2=tar_file2.readlines()
            for i2 in line2[1:-1]:
                i2=i2.strip() 
                neg_id=i2[6:11]
                neg_target_B.append(neg_id)
    #print(neg_target)
    tt_B=all_target_B
    new_target_B=all_target_B
        
                #print(new_target)
    for numm,i55 in enumerate(tt_B):
                    for i66 in neg_target_B:
                        if i66==i55:
                            new_target_B[numm]=0
    for num,i5 in enumerate(tt_B):
                    for i6 in pos_target_B:
                        if i6==i5:
                            new_target_B[num]=1 
    
    
    target_all=new_target+new_target_B
    input_file=os.path.join(save_npz_path,"%s.npz"%pdb_name)
    np.savez(input_file,  H=final_feature, A1=combined_matrix, T=target_all)

目前正在处理的是：1A0H_1_A_B_B.pdb
目前正在处理的是：1A0H_1_A_B_A.pdb
torch.Size([418, 1280])
A链的特征矩阵的大小为:torch.Size([152, 30]),A链的邻接矩阵的小为(152, 152)
B链的特征矩阵的大小为:torch.Size([134, 30]),B链的邻接矩阵的小为(134, 134)
lenth2的长度为： 134 lenth1的长度为： 152
合并后的邻接矩阵大小combined_matrix为： (286, 286)
[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151]
[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 2